In [1]:
import numpy as np
%matplotlib inline
import matplotlib.pyplot as plt
from ipywidgets import interact, interact_manual
from numpy import fft

## trasformate di fourier, osservazioni base


la trasformata discreta di fourier è una trasformazione di una funzione definita in un intervallo di interi [0,n-1] ad un'altra definita sullo stesso intervallo. la trasformata di fourier veloce, fft, richiede che l'intervallo di interi sia caratterizzato da n con fattori piccoli, in molti casi n può essere solo una potenza di 2.

In [2]:
def delta(log_lunghezza, posizione):
    res=np.zeros(2**log_lunghezza)
    res[posizione]=1
    return res

@interact_manual(pos=(0,128,1))
def rendi_fft(pos=0):
    x=np.linspace(0,255,256)
    diretta=delta(8,pos)
    x
    diretta
    
    inversa=fft.fft(diretta,norm="ortho")
    (fig, (ax1, ax2, ax3)) = plt.subplots(nrows=3, figsize=(9,14))
    ax1.plot(x, diretta)
    ax2.plot(x, np.real(inversa), label="reale")
    ax2.plot(x, np.imag(inversa), label="immaginaria")
    ax2.legend()
    ax3.plot(fft.fftshift(fft.fftfreq(256,d=1)), np.real(fft.fftshift(inversa)))
    plt.show()
    

A Jupyter Widget

nella terza sottofigura abbiamo effettuato due operazioni di rito rispetto alla sottofigura 2:
1. abbiamo usato fftshift per centrare l'intervallo dei numeri d'onda invece che farlo partire da 0
2. abbiamo scalato l'asse tramite la funzione fftfreq, che ci restituisce il giusto intervallo per l'asse delle ascisse della trasformata, [-pi/x_max,pi/x_max[


vediamo la trasformata di fourier di una gaussiana.
osserviamo che:
* traslando la gaussiana, la trasformata cambia solo per il fattore di fase, la trasformata della gaussiana centrata in O è una funzione reale;
* ad una gaussiana stretta nello spazio diretto corrisponde una gaussiana larga nello spazio inverso


In [ ]:

def una_gaussiana_periodicizzata(x, sigma, pos):
    res=x*0
    scala=1/2/sigma**2
    intervallo=len(x)*(x[1]-x[0])
    for i in np.arange(-3,4):
        u=x+i*intervallo-pos
        res += np.exp(-u*u*scala)
    return res

@interact_manual(pos=(0.0, 1.0, 0.01), sigma=(0.025,0.2, 0.025))
def guarda_gauss(pos=0.0, sigma=0.1):
    x=np.linspace(0.0, 1.0, 256, endpoint=False)
    y=una_gaussiana_periodicizzata(x,sigma,pos)
    (fig, (ax1, ax2, ax3)) = plt.subplots(nrows=3, figsize=(9,14))
    ax1.plot(x, y)
    y_inv=fft.fft(y, norm="ortho")
    x_inv=np.linspace(0.0, 256.0, 256, endpoint=False)
    ax2.plot(x_inv, np.real(y_inv), label="reale")
    ax2.plot(x_inv, np.imag(y_inv), label="imag")
    ax2.legend()
    # ax3.plot(x_inv, np.abs(y_inv), label="abs")
    # fase=y_inv
    # fase[np.real(y_inv) >= -5.0e-9] += 1e-8
    # fase=np.angle(fase)
    # ax3.plot(x_inv, fase, label="fase")
    # ax3.legend()
    ax3.plot(fft.fftshift(fft.fftfreq(256, d=1.0/256)), np.abs(fft.fftshift(y_inv)))
    plt.show()

    

il comportamento della trasformata di fourier rispetto alla convoluzione è determinante per la scelta delle funzioni di apodizzazione delle spettroscopie in ft.
consideriamo uno spettro ed il suo interferogramma, essenzialmente la sua trasformata di fourier troncata nel tempo.
Useremo per semplicità uno spettro sintetico.

In [ ]:
x=np.linspace(0.0, 1.0, 2048, endpoint=False)
def spettro_sintetico(x, w, ww, n):
    '''spettro sintetico, n picchi larghi w spaziati ww'''
    x0=(x[0]+x[-1])*0.5 - ww*n/2  # posizione del primo picco dello spettro
    res=x*0.0
    scala=0.5/w**2
    for i in range(n):
        u=x-(x0+i*ww)
        res=res+np.exp(-u*u*scala)
    return res

y=spettro_sintetico(x, 0.003, 0.1, 5)
plt.plot(x,y)
plt.show()

    

se trasformiamo lo spettro nel completo interferogramma e viceversa, riotterremo lo spettro inalterato

In [ ]:
y_inv=fft.fft(y)
y_d=fft.ifft(y_inv)
#plt.plot(x[0:1024//2],y_d)
(fig, (ax1, ax2)) = plt.subplots(nrows=2, figsize=(9,14))
ax1.plot(x,np.real(y_inv))
ax2.plot(x,np.real(y_d))
plt.show()


lo stesso avviene se tronco una parte inessenziale dell'interferogramma ma se invece tronco una parte non nulla dell'interferogramma:

In [ ]:
@interact_manual(divisore=[2,4,8,16,32])
def tronca(divisore=2):
   y_d=fft.ifft(y_inv[0:2048//divisore])
   plt.plot(x[0:2048//divisore],np.real(y_d))
   plt.show()


per regolarizzare l'interferogramma e farci restituire uno spettro con un numero minore di artefatti utilizziamo la funzione apodizzazione, una funzione a forma di campana che moltiplica l'interferogramma ed elimina le irregolarità ai bordi. ma un effetto di operare con l'apodizzazione può essere un allargamento delle righe. 



In [ ]:
@interact_manual(divisore=[2,4,8,16,32], apodiz={'boxcar': 0, 'weak': 2, 'medium': 3, 'strong' :4})
def tronca(apodiz, divisore=2):
   y_inv_tronc=y_inv[0:2048//divisore]
   supp=np.linspace(0.0, 1.0, 2048//divisore, endpoint=False)
   y_inv_tronc=y_inv_tronc*np.exp(-apodiz*supp*supp)
   y_d=fft.ifft(y_inv_tronc)
   plt.plot(x[0:2048//divisore],np.real(y_d))
   plt.show()


#### esercizio


Ora definite una funzione nello spazio diretto, per esempio una gaussiana ed una funzione di apodizzazione. Osservate su un grafico come è fatta la trasformata inversa della funzione apodizzazione. Poi moltiplicate la funzione di apodizzazione per la trasformata dello spettro (interferogramma) e fatene la trasformata inversa. Sovrapponetene il grafico a quello dello spettro originale.
